# Prepare Leaf venation type data from TRY for use

The Leaf venation type data from TRY informs about the leaf vein arrangement and about whether leaf veins
are open or closed.

*If you intend to clean more than one or two traits, we recommend the use of the batch pre-processing script. Refer to the [TRY main page](try-label) for details.*

If you have questions, suggestions, spot errors, or want to contribute, get in touch with us through planthub@idiv.de.

Author: David Schellenberger Costa

## Requirements

To run the script, the following is needed:
- TRY data, available <a href="https://planthub.idiv.de/downloads/" target="_parent">here</a>
- the data.table library may need to be installed

## Code

In [ ]:
# load in libraries
library(data.table) # handle large datasets

# clear workspace
rm(list = ls())


Let's get the TRY data

In [ ]:
# set working directory (adapt this!)
setwd(paste0(.brd, "PlantHub"))

# read in data (adapt this!)
TRY <- fread("TRY_PlantHub.gz")

# select data of interest
TRYSubset <- TRY[TraitName == "Leaf venation type"]


To get an overview of the data, we convert values to lowercase, sort them, and show them as
a table.

In [ ]:
# extract original data strings
oriVals <- TRYSubset$OrigValueStr # oriVals == original values

# change all to lowercase to ease later classification
oriVals <- tolower(oriVals)

# get an overview over the data by summarizing values and showing them in alphabetical order
valueOverview <- table(oriVals)
valueOverview[order(valueOverview)]


Some entries are just the word "yes" or "10", while the actual data can be found in the OriglName column. This should be decoded. We also remove purely numeric values.

In [ ]:
# decode coded entries
oriVals[TRYSubset$DatasetID == 319 & oriVals %in% c("yes", "10")] <-
	TRYSubset[TRYSubset$DatasetID == 319 & oriVals %in% c("yes", "10")]$OriglName

# remove purely numeric values and others that have no lowercase character included
oriVals[!grepl("[[:lower:]]", oriVals)] <- NA


The most important part of the cleaning process is the definition of the search strings to look for.
We use regular expressions in some cases to be more inclusive (or exclusive).

In [ ]:
# create a vector containing the search strings to look for
searchNames <- c(
	# leaf venation type
	"palmate",
	"parallel",
	"pinnate",
	"triplinerve",
	"open",
	"intermediate",
	"closed"
)


We can now search for the strings defined before and give names to the new categories.

In [ ]:
# search for the strings defined before
searchResults <- sapply(searchNames, grepl, oriVals, ignore.case = TRUE)

# name columns of searchResults matrix like corrected searchNames
colnames(searchResults) <- searchNames


Let's have a look at the results.

In [ ]:
# show the number of matches to each category
colSums(searchResults)

# show the original entries for which no match was retrieved
sort(table(oriVals[rowSums(searchResults) < 1]))

# show the number of entries that weren't matched to any category
sum(rowSums(searchResults) < 1)

# show the number of entries that were matched to more that one category
sum(rowSums(searchResults) > 1)


As some values are mutually exclusive, we remove ambiguous entries.

In [ ]:
# remove contradictory entries
searchResults[
	rowSums(searchResults[, grep("open|intermediate|closed", colnames(searchResults))]) > 1,
	grep("open|intermediate|closed", colnames(searchResults))
] <- FALSE
searchResults[
	rowSums(searchResults[, grep("palmate|pinnate", colnames(searchResults))]) > 1,
	grep("palmate|pinnate", colnames(searchResults))
] <- FALSE


We can now use the cleaned results data to create a new data vector.

In [ ]:
# use the searchResults matrix to create new value strings by concatenating all data found
newVals <- sapply(seq_len(nrow(searchResults)), function(x) {
	paste(colnames(searchResults)[searchResults[x, ]], collapse = ",")
})
newVals[newVals == ""] <- NA


Let's transfer the data into the original data frame.

In [ ]:
# integrate into TRY
TRY[TraitName == "Leaf venation type", CleanedValueStr := newVals]


Let's write the data to a file.

In [ ]:
# write data
fwrite(TRY, file = paste0("TRY_processed_", Sys.Date(), ".gz"))
